# Vietinis reguliarusis susisiekimas
Toliau pateikiami analizuoti viešojo transporto kelionių duomenys esantys VINTRA susiję su vietiniu reguliariuoju (miesto ir priemesčio) susisiekimu.



In [ ]:
import json
import os
from zipfile import ZipFile
from typing import Optional

import pandas as pd
import plotly.express as px
import requests

working_directory = f'{os.getcwd()}/../data/saltiniai/vintra/'
stops_lt_directory = f'{os.getcwd()}/../data/saltiniai/stops-lt/'
gtfs_files_directory = os.path.join(working_directory, 'gtfs')
stops_lt_gtfs_directory = os.path.join(stops_lt_directory, 'gtfs')
netex_directory = os.path.join(working_directory, 'netex')

mapbox_access_token = open("../.mapbox_token").read()
px.set_mapbox_access_token(mapbox_access_token)

lithuania_center = {'lat': 55.169438, 'lon': 23.881275}

municipalities_gtfs_file_mapping = pd.read_csv(
    os.path.join(working_directory, 'vintra-gtfs-file-mapping.csv'),
    na_filter=False)
vintra_netex_mapping = pd.read_csv(os.path.join(working_directory, 'vintra-netex-file-mapping.csv'), na_filter=False)
stops_lt_gtfs_mapping = pd.read_csv(os.path.join(stops_lt_directory, 'stops-lt-file-mapping.csv'), na_filter=False)

with open('../data/geojson/municipalities.geojson', 'r') as municipalities_geojson_file:
    municipalities_geojson = json.load(municipalities_geojson_file)


In [ ]:
# municipalities_files_mapping = pd.merge(municipalities_gtfs_file_mapping, vintra_netex_mapping, on='Savivaldybe',
#                                         suffixes=('_gtfs', '_netex'))
#
# municipalities_files_mapping['gtfs'] = municipalities_files_mapping['Failas_gtfs'].apply(
#     lambda x: f'[{x}](https://www.visimarsrutai.lt/gtfs/{x})')
#
# municipalities_files_mapping['netex'] = municipalities_files_mapping['Failas_netex'].apply(
#     lambda x: f'[{x}](https://www.visimarsrutai.lt/netex/{x})')
#
# municipalities_files_mapping.to_markdown()

## Duomenų failai pagal savivaldybes
```{admonition} 8 savivaldybių duomenys nėra pateikiami NeTEx formatu
:class: warning

NeTEx formatu nepateikiami 8 savivaldybių viešojo transporto kelionių duomenys (Alytaus, Biržų, Jurbarko, Kėdainių, Kelmės, Kupiškio, Mažeikių, Rokiškio, Vilniaus rajono savivaldybių). Dėl šios priežasties nėra galimybės naudoti šių savivaldybių viešojo transporto duomenų NeTEx formatu.
```

```{admonition} 3 savivaldybių duomenys nėra pateikiami GTFS formatu
:class: warning

GTFS formatu nepateikiami 3 savivaldybių viešojo transporto kelionių duomenys (Šakių, Širvintų, Telšių rajono savivaldybių). Dėl šios priežasties nėra galimybės naudoti šių savivaldybių viešojo transporto duomenų GTFS formatu.
```

```{admonition} Nepateikiami GTFS ir NeTEx priklauso skirtingoms savivaldybėms
:class: info

Atsižvelgiant į tai, kad skirtingų savivaldybių viešojo transporto kelionių duomenys nėra pateikiami GTFS ir NeTEx formatais galima manyti, kad duomenų failai nėra pateikiami dėl VINTRA sisteminės klaidos.
```

```{table} VINTRA duomenų failai pagal savivaldybes. Duomenys surinkti 2022 m. gegužės 12 d.
:name: data-files-municipalities-vintra

| Savivaldybė                    | GTFS                                                                   | NeTEx                                                                         |
|--------------------------------|------------------------------------------------------------------------|-------------------------------------------------------------------------------|
| Akmenės rajono savivaldybė     | [akmene.zip](https://www.visimarsrutai.lt/gtfs/akmene.zip)             | [Akmenesraj.zip](https://www.visimarsrutai.lt/netex/Akmenesraj.zip)           |
| Alytaus miesto savivaldybė     | [AlytausM.zip](https://www.visimarsrutai.lt/gtfs/AlytausM.zip)         | [Alytausm.zip](https://www.visimarsrutai.lt/netex/Alytausm.zip)               |
| Alytaus rajono savivaldybė     | [AlytausR.zip](https://www.visimarsrutai.lt/gtfs/AlytausR.zip)         | ❌                                                                             |
| Anykščių rajono savivaldybė    | [AnyksciuR.zip](https://www.visimarsrutai.lt/gtfs/AnyksciuR.zip)       | [Anyksciuraj.zip](https://www.visimarsrutai.lt/netex/Anyksciuraj.zip)         |
| Birštono savivaldybė           | [Birstono.zip](https://www.visimarsrutai.lt/gtfs/Birstono.zip)         | [Birstonoraj.zip](https://www.visimarsrutai.lt/netex/Birstonoraj.zip)         |
| Biržų rajono savivaldybė       | [BirzuR.zip](https://www.visimarsrutai.lt/gtfs/BirzuR.zip)             | ❌                                                                             |
| Druskininkų savivaldybė        | [Druskininku.zip](https://www.visimarsrutai.lt/gtfs/Druskininku.zip)   | [Druskininkuraj.zip](https://www.visimarsrutai.lt/netex/Druskininkuraj.zip)   |
| Elektrėnų savivaldybė          | [Elektrenu.zip](https://www.visimarsrutai.lt/gtfs/Elektrenu.zip)       | [Elektrenusav.zip](https://www.visimarsrutai.lt/netex/Elektrenusav.zip)       |
| Ignalinos rajono savivaldybė   | [IgnalinosR.zip](https://www.visimarsrutai.lt/gtfs/IgnalinosR.zip)     | [Ignalinosraj.zip](https://www.visimarsrutai.lt/netex/Ignalinosraj.zip)       |
| Jonavos rajono savivaldybė     | [JonavosR.zip](https://www.visimarsrutai.lt/gtfs/JonavosR.zip)         | [Jonavosraj.zip](https://www.visimarsrutai.lt/netex/Jonavosraj.zip)           |
| Joniškio rajono savivaldybė    | [JoniskioR.zip](https://www.visimarsrutai.lt/gtfs/JoniskioR.zip)       | [Joniskioraj.zip](https://www.visimarsrutai.lt/netex/Joniskioraj.zip)         |
| Jurbarko rajono savivaldybė    | [JurbarkoR.zip](https://www.visimarsrutai.lt/gtfs/JurbarkoR.zip)       | ❌                                                                             |
| Kaišiadorių rajono savivaldybė | [KiasiadoriuR.zip](https://www.visimarsrutai.lt/gtfs/KiasiadoriuR.zip) | [Kaisiadoriuraj.zip](https://www.visimarsrutai.lt/netex/Kaisiadoriuraj.zip)   |
| Kalvarijos savivaldybė         | [Kalvarijos.zip](https://www.visimarsrutai.lt/gtfs/Kalvarijos.zip)     | [Kalvarijosraj.zip](https://www.visimarsrutai.lt/netex/Kalvarijosraj.zip)     |
| Kauno miesto savivaldybė       | [KaunoM.zip](https://www.visimarsrutai.lt/gtfs/KaunoM.zip)             | [Kaunom.zip](https://www.visimarsrutai.lt/netex/Kaunom.zip)                   |
| Kauno rajono savivaldybė       | [KaunoR.zip](https://www.visimarsrutai.lt/gtfs/KaunoR.zip)             | [Kaunoraj.zip](https://www.visimarsrutai.lt/netex/Kaunoraj.zip)               |
| Kazlų Rūdos savivaldybė        | [Kazlurudos.zip](https://www.visimarsrutai.lt/gtfs/Kazlurudos.zip)     | [Kazlurudosraj.zip](https://www.visimarsrutai.lt/netex/Kazlurudosraj.zip)     |
| Kėdainių rajono savivaldybė    | [KedainiuR.zip](https://www.visimarsrutai.lt/gtfs/KedainiuR.zip)       | ❌                                                                             |
| Kelmės rajono savivaldybė      | [KelmesR.zip](https://www.visimarsrutai.lt/gtfs/KelmesR.zip)           | ❌                                                                             |
| Klaipėdos miesto savivaldybė   | [KlaipedosM.zip](https://www.visimarsrutai.lt/gtfs/KlaipedosM.zip)     | [Klaipedosm.zip](https://www.visimarsrutai.lt/netex/Klaipedosm.zip)           |
| Klaipėdos rajono savivaldybė   | [KlaipedosR.zip](https://www.visimarsrutai.lt/gtfs/KlaipedosR.zip)     | [Klaipedosraj.zip](https://www.visimarsrutai.lt/netex/Klaipedosraj.zip)       |
| Kretingos rajono savivaldybė   | [KretingosR.zip](https://www.visimarsrutai.lt/gtfs/KretingosR.zip)     | [Kretingosraj.zip](https://www.visimarsrutai.lt/netex/Kretingosraj.zip)       |
| Kupiškio rajono savivaldybė    | [KupiskioR.zip](https://www.visimarsrutai.lt/gtfs/KupiskioR.zip)       | ❌                                                                             |
| Lazdijų rajono savivaldybė     | [LazdijuR.zip](https://www.visimarsrutai.lt/gtfs/LazdijuR.zip)         | [Lazdijuraj.zip](https://www.visimarsrutai.lt/netex/Lazdijuraj.zip)           |
| Marijampolės savivaldybė       | [Marijampoles.zip](https://www.visimarsrutai.lt/gtfs/Marijampoles.zip) | [Marijampolesraj.zip](https://www.visimarsrutai.lt/netex/Marijampolesraj.zip) |
| Mažeikių rajono savivaldybė    | [MazeikiuR.zip](https://www.visimarsrutai.lt/gtfs/MazeikiuR.zip)       | ❌                                                                             |
| Molėtų rajono savivaldybė      | [MoletuR.zip](https://www.visimarsrutai.lt/gtfs/MoletuR.zip)           | [Moleturaj.zip](https://www.visimarsrutai.lt/netex/Moleturaj.zip)             |
| Neringos savivaldybė           | [neringa.zip](https://www.visimarsrutai.lt/gtfs/neringa.zip)           | [Neringosraj.zip](https://www.visimarsrutai.lt/netex/Neringosraj.zip)         |
| Pagėgių savivaldybė            | [PagegiuR.zip](https://www.visimarsrutai.lt/gtfs/PagegiuR.zip)         | [Pagegiuraj.zip](https://www.visimarsrutai.lt/netex/Pagegiuraj.zip)           |
| Pakruojo rajono savivaldybė    | [PakruojoR.zip](https://www.visimarsrutai.lt/gtfs/PakruojoR.zip)       | [Pakruojoraj.zip](https://www.visimarsrutai.lt/netex/Pakruojoraj.zip)         |
| Palangos miesto savivaldybė    | [PalangosM.zip](https://www.visimarsrutai.lt/gtfs/PalangosM.zip)       | [Palangosm.zip](https://www.visimarsrutai.lt/netex/Palangosm.zip)             |
| Panevėžio miesto savivaldybė   | [PanevezioM.zip](https://www.visimarsrutai.lt/gtfs/PanevezioM.zip)     | [Paneveziom.zip](https://www.visimarsrutai.lt/netex/Paneveziom.zip)           |
| Panevėžio rajono savivaldybė   | [PanevezioR.zip](https://www.visimarsrutai.lt/gtfs/PanevezioR.zip)     | [Panevezioraj.zip](https://www.visimarsrutai.lt/netex/Panevezioraj.zip)       |
| Pasvalio rajono savivaldybė    | [PasvalioR.zip](https://www.visimarsrutai.lt/gtfs/PasvalioR.zip)       | [Pasvalioraj.zip](https://www.visimarsrutai.lt/netex/Pasvalioraj.zip)         |
| Plungės rajono savivaldybė     | [PlungesR.zip](https://www.visimarsrutai.lt/gtfs/PlungesR.zip)         | [Plungesraj.zip](https://www.visimarsrutai.lt/netex/Plungesraj.zip)           |
| Prienų rajono savivaldybė      | [PrienuR.zip](https://www.visimarsrutai.lt/gtfs/PrienuR.zip)           | [Prienuraj.zip](https://www.visimarsrutai.lt/netex/Prienuraj.zip)             |
| Radviliškio rajono savivaldybė | [RadviliskioR.zip](https://www.visimarsrutai.lt/gtfs/RadviliskioR.zip) | [Radviliskioraj.zip](https://www.visimarsrutai.lt/netex/Radviliskioraj.zip)   |
| Raseinių rajono savivaldybė    | [RaseiniuR.zip](https://www.visimarsrutai.lt/gtfs/RaseiniuR.zip)       | [Raseiniuraj.zip](https://www.visimarsrutai.lt/netex/Raseiniuraj.zip)         |
| Rietavo savivaldybė            | [Rietavo.zip](https://www.visimarsrutai.lt/gtfs/Rietavo.zip)           | [Rietavoraj.zip](https://www.visimarsrutai.lt/netex/Rietavoraj.zip)           |
| Rokiškio rajono savivaldybė    | [RokiskioR.zip](https://www.visimarsrutai.lt/gtfs/RokiskioR.zip)       | ❌                                                                             |
| Šakių rajono savivaldybė       | ❌                                                                      | [Sakiuraj.zip](https://www.visimarsrutai.lt/netex/Sakiuraj.zip)               |
| Šalčininkų rajono savivaldybė  | [SalcininkuR.zip](https://www.visimarsrutai.lt/gtfs/SalcininkuR.zip)   | [Salcininkuraj.zip](https://www.visimarsrutai.lt/netex/Salcininkuraj.zip)     |
| Šiaulių miesto savivaldybė     | [SiauliuM.zip](https://www.visimarsrutai.lt/gtfs/SiauliuM.zip)         | [Siaulium.zip](https://www.visimarsrutai.lt/netex/Siaulium.zip)               |
| Šiaulių rajono savivaldybė     | [SiauliuR.zip](https://www.visimarsrutai.lt/gtfs/SiauliuR.zip)         | [Siauliuraj.zip](https://www.visimarsrutai.lt/netex/Siauliuraj.zip)           |
| Šilalės rajono savivaldybė     | [SilalesR.zip](https://www.visimarsrutai.lt/gtfs/SilalesR.zip)         | [Silalesraj.zip](https://www.visimarsrutai.lt/netex/Silalesraj.zip)           |
| Šilutės rajono savivaldybė     | [SilutesR.zip](https://www.visimarsrutai.lt/gtfs/SilutesR.zip)         | [Silutesraj.zip](https://www.visimarsrutai.lt/netex/Silutesraj.zip)           |
| Širvintų rajono savivaldybė    | ❌                                                                      | [Sirvinturaj.zip](https://www.visimarsrutai.lt/netex/Sirvinturaj.zip)         |
| Skuodo rajono savivaldybė      | [SkuodoR.zip](https://www.visimarsrutai.lt/gtfs/SkuodoR.zip)           | [Skuodoraj.zip](https://www.visimarsrutai.lt/netex/Skuodoraj.zip)             |
| Švenčionių rajono savivaldybė  | [SvencioniuR.zip](https://www.visimarsrutai.lt/gtfs/SvencioniuR.zip)   | [Svencioniuraj.zip](https://www.visimarsrutai.lt/netex/Svencioniuraj.zip)     |
| Tauragės rajono savivaldybė    | [TauragesR.zip](https://www.visimarsrutai.lt/gtfs/TauragesR.zip)       | [Tauragesraj.zip](https://www.visimarsrutai.lt/netex/Tauragesraj.zip)         |
| Telšių rajono savivaldybė      | ❌                                                                      | [Telsiuraj.zip](https://www.visimarsrutai.lt/netex/Telsiuraj.zip)             |
| Trakų rajono savivaldybė       | [TrakuR.zip](https://www.visimarsrutai.lt/gtfs/TrakuR.zip)             | [Trakuraj.zip](https://www.visimarsrutai.lt/netex/Trakuraj.zip)               |
| Ukmergės rajono savivaldybė    | [UkmergesR.zip](https://www.visimarsrutai.lt/gtfs/UkmergesR.zip)       | [Ukmergesraj.zip](https://www.visimarsrutai.lt/netex/Ukmergesraj.zip)         |
| Utenos rajono savivaldybė      | [UtenosR.zip](https://www.visimarsrutai.lt/gtfs/UtenosR.zip)           | [Utenosraj.zip](https://www.visimarsrutai.lt/netex/Utenosraj.zip)             |
| Varėnos rajono savivaldybė     | [VarenosR.zip](https://www.visimarsrutai.lt/gtfs/VarenosR.zip)         | [Varenosraj.zip](https://www.visimarsrutai.lt/netex/Varenosraj.zip)           |
| Vilkaviškio rajono savivaldybė | [VilkaviskioR.zip](https://www.visimarsrutai.lt/gtfs/VilkaviskioR.zip) | [Vilkaviskioraj.zip](https://www.visimarsrutai.lt/netex/Vilkaviskioraj.zip)   |
| Vilniaus miesto savivaldybė    | [VilniausM.zip](https://www.visimarsrutai.lt/gtfs/VilniausM.zip)       | [Vilniausm.zip](https://www.visimarsrutai.lt/netex/Vilniausm.zip)             |
| Vilniaus rajono savivaldybė    | [VilniausR.zip](https://www.visimarsrutai.lt/gtfs/VilniausR.zip)       | ❌                                                                             |
| Visagino savivaldybė           | [VisaginoM.zip](https://www.visimarsrutai.lt/gtfs/VisaginoM.zip)       | [Visaginoraj.zip](https://www.visimarsrutai.lt/netex/Visaginoraj.zip)         |
| Zarasų rajono savivaldybė      | [ZarasuR.zip](https://www.visimarsrutai.lt/gtfs/ZarasuR.zip)           | [Zarasuraj.zip](https://www.visimarsrutai.lt/netex/Zarasuraj.zip)             |
```

In [ ]:
# from zipfile import BadZipFile
#
#
# def has_non_empty_gtfs_file(file: str, gtfs_file: str) -> bool:
#     if not file:
#         return False
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#
#         if gtfs_file not in gtfs_zip_files:
#             return False
#
#         try:
#             with gtfs_zip.open(gtfs_file) as zip_file:
#                 return pd.read_csv(zip_file).shape[0] > 0
#         except BadZipFile:
#             return False
#
#
# gtfs_files_by_specification = [
#     'agency.txt',
#     'stops.txt',
#     'routes.txt',
#     'trips.txt',
#     'stop_times.txt',
#     'routes.txt',
#     'trips.txt',
#     'stop_times.txt',
#     'calendar.txt',
#     'calendar_dates.txt',
#     'shapes.txt',
#     'feed_info.txt',
#     'fare_rules.txt',
#     'fare_attributes.txt',
#     'translations.txt',
#     'frequencies.txt',
#     'transfers.txt',
#     'pathways.txt',
#     'levels.txt',
#     'attributions.txt',
# ]
#
# municipalities_files_availability = municipalities_gtfs_file_mapping.copy()
#
# for gtfs_file_by_specification in gtfs_files_by_specification:
#     municipalities_files_availability[gtfs_file_by_specification] = municipalities_files_availability.apply(
#         lambda m: has_non_empty_gtfs_file(m['Failas'], gtfs_file_by_specification), axis=1).astype(int)
#
#
#  municipalities_files_availability['sum'] = municipalities_files_availability['agency.txt'] + municipalities_files_availability['stops.txt'] + municipalities_files_availability['routes.txt'] + municipalities_files_availability['trips.txt'] + municipalities_files_availability['stop_times.txt']
#
#  municipalities_files_availability[municipalities_files_availability['sum'] != 5].sort_values('Savivaldybe').to_excel('missing-required-files.xlsx')
#
# municipalities_files_availability

## Privalomi GTFS duomenų rinkinio failai
Pagal [specifikaciją](https://gtfs.org/schedule/reference/#dataset-files) GTFS privalo sudaryti bent penki failai (`agency.txt`, `stops.txt`, `routes.txt`, `trips.txt`, `stop_times.txt`).

Toliau esančioje lentelėje matomos savivaldybės, kurių GTFS duomenų rinkinyje trūksta bent vieno privalomo failo.

```{admonition} 23 savivaldybių GTFS duomenų rinkiniams trūksta bent vieno privalomo failo
:class: warning
23 savivaldybių GTFS duomenų rinkiniams trūksta bent vieno privalomo failo. Tai reiškia, kad 23 savivaldybės ilgą laiką neatnaujino duomenų ir nebėra pateikiama jokia keleiviams aktuali viešojo transporto informacija.
```

```{admonition} Birštono savivaldybės GTFS failas yra sugadintas
:class: warning
Birštono savivaldybės GTFS failas yra sugadintas ir negali būti atidarytas. Bandymas naudoti tokį GTFS failą gali sukelti papildomų nepatogumų bandant nuskaityti failą automatiniu būdu.
```

```{table} VINTRA savivaldybių GTFS duomenų rinkiniai, kuriems trūksta bent vieno privalomo failą. Duomenys surinkti 2022 m. gegužės 12 d.
:name: data-files-municipalities-missing-required-file

| Savivaldybė                    | agency.txt | stops.txt | routes.txt | trips.txt | stop\_times.txt |
|--------------------------------|------------|-----------|------------|-----------|-----------------|
| Birštono savivaldybė           | ❌          | ❌         | ❌          | ❌         | ❌               |
| Elektrėnų savivaldybė          | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Joniškio rajono savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kaišiadorių rajono savivaldybė | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kazlų Rūdos savivaldybė        | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kėdainių rajono savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kelmės rajono savivaldybė      | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kretingos rajono savivaldybė   | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Kupiškio rajono savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Lazdijų rajono savivaldybė     | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Molėtų rajono savivaldybė      | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Pagėgių savivaldybė            | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Palangos miesto savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Panevėžio rajono savivaldybė   | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Pasvalio rajono savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Plungės rajono savivaldybė     | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Radviliškio rajono savivaldybė | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Raseinių rajono savivaldybė    | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Rietavo savivaldybė            | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Šilalės rajono savivaldybė     | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Skuodo rajono savivaldybė      | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Trakų rajono savivaldybė       | ✔️         | ❌         | ❌          | ❌         | ❌               |
| Vilkaviškio rajono savivaldybė | ✔️         | ❌         | ❌          | ❌         | ❌               |
```

In [ ]:
# municipalities_valid_routes_df = municipalities_gtfs_file_mapping.copy()
#
#
# def calculate_total_routes(file: str) -> int:
#     if not file:
#         return -1
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#         if "routes.txt" not in gtfs_zip_files:
#             return -1
#
#         routes_df = pd.read_csv(gtfs_zip.open("routes.txt"))
#         return routes_df['route_id'].nunique()
#
#
# def calculate_total_trips(file: str) -> int:
#     if not file:
#         return -1
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#         if "trips.txt" not in gtfs_zip_files:
#             return -1
#
#         trips_df = pd.read_csv(gtfs_zip.open("trips.txt"))
#         return trips_df['trip_id'].nunique()
#
#
# def calculate_valid_routes(file: str) -> float:
#     if not file:
#         return -1
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#         if "calendar.txt" not in gtfs_zip_files or "routes.txt" not in gtfs_zip_files or "trips.txt" not in gtfs_zip_files:
#             return -1
#
#         routes_df = pd.read_csv(gtfs_zip.open("routes.txt"))
#         calendar_df = pd.read_csv(gtfs_zip.open("calendar.txt"), parse_dates=['start_date', 'end_date'])
#         trips_df = pd.read_csv(gtfs_zip.open("trips.txt"))
#
#         merged_df = trips_df.merge(calendar_df, on='service_id')
#
#         total_routes = routes_df['route_id'].nunique()
#         if total_routes == 0:
#             return 0
#
#         valid_routes = merged_df[(merged_df['end_date'] >= '2022-04-08')]['route_id'].nunique()
#
#         return valid_routes / total_routes
#
#
# def calculate_last_valid_trip_date_formatted(file: str) -> str:
#     if not file:
#         return '-'
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#         if "calendar.txt" not in gtfs_zip_files:
#             return '-'
#
#         calendar_df = pd.read_csv(gtfs_zip.open("calendar.txt"), parse_dates=['start_date', 'end_date'])
#         max_end_date = calendar_df['end_date'].max()
#
#         return f'{max_end_date.date()}' if max_end_date else '-'
#
#
# def calculate_average_trip_validity(file: str):
#     if not file:
#         return '-'
#
#     with ZipFile(os.path.join(gtfs_files_directory, file)) as gtfs_zip:
#         gtfs_zip_files = gtfs_zip.namelist()
#         if "calendar.txt" not in gtfs_zip_files:
#             return '-'
#
#         calendar_df = pd.read_csv(gtfs_zip.open("calendar.txt"), parse_dates=['start_date', 'end_date'])
#         calendar_df['duration'] = calendar_df['end_date'].dt.to_period('M').astype(int) - calendar_df[
#             'start_date'].dt.to_period('M').astype(int)
#
#         max_duration = calendar_df['duration'].median()
#
#         return f'{max_duration}' if max_duration else '-'
#
#
# municipalities_valid_routes_df['Maršrutai'] = municipalities_valid_routes_df.apply(
#     lambda m: calculate_total_routes(m['Failas']), axis=1)
#
# municipalities_valid_routes_df['Reisai'] = municipalities_valid_routes_df.apply(
#     lambda m: calculate_total_trips(m['Failas']), axis=1)
#
# municipalities_valid_routes_df['Maršrutų su galiojančiais reisais dalis (%)'] = municipalities_valid_routes_df.apply(
#     lambda m: calculate_valid_routes(m['Failas']), axis=1)
#
# municipalities_valid_routes_df['Didžiausia reiso galiojimo data'] = municipalities_valid_routes_df.apply(
#     lambda m: calculate_last_valid_trip_date_formatted(m['Failas']), axis=1)
#
# municipalities_valid_routes_df['Reisų galiojimo trukmės mediana (mėnesiais)'] = municipalities_valid_routes_df.apply(
#     lambda m: calculate_average_trip_validity(m['Failas']), axis=1)
# municipalities_valid_routes_df[municipalities_valid_routes_df['Maršrutai'] > 0].to_excel('validity.xlsx')

## Maršrutai
Kiekvienas maršrutas susideda ir vieno ar keleto reisų, kurie turi galiojimo laiką. Kai duomenys ilgą laiką nėra atnaujinami reisai nustoja galioti, ir maršrutai lieka be jokių galiojančių reisų. Toliau pateikiamos savivaldybės, kuriose dalis maršrutų liko be galiojančių reisų.

```{admonition} 2 savivaldybėse dalis maršrutų neturi galiojančių reisų
:class: warning
Jovanos ir Klaipėdos rajono savivaldybių viešojo transporto kelionių duomenyse dalis maršrutų nebeturi nė vieno galiojančio reiso. Tai indikacija, kad duomenys šiose savivaldybėse nėra atnaujinami reguliariai.
```

```{table} GTFS savivaldybių failai, kurių bent vienas maršrutas neturi nė vieno galiojančio reiso
:name: municipalities-valid-routes

| Savivaldybė                  | Maršrutai | Reisai | Maršrutų su galiojančiais reisais dalis |
|------------------------------|-----------|--------|-----------------------------------------|
| Jonavos rajono savivaldybė   | 3         | 8      | 67%                                     |
| Klaipėdos rajono savivaldybė | 2         | 6      | 50%                                     |
```



## Reisai
Įprastai vietinis reguliarusis susisiekimas turi vasaros ir žiemos arba visus metus galiojančius tvarkaraščius. Tvarkaraščio galiojimo laikui nustatyti duomenų teikėjas reisui priskiria galiojimo laiką. Galiojimo trukmė turėtų būti atitikti tvarkaraščio galiojimo trukmę pvz., tvarkaraštis turėtų galioji ne daugiau nei 2-3 metus. Vis dėlto ilgas reiso galiojimo laikas nebūtinai reiškia nepatikimus duomenis.

```{admonition} 13 savivaldybių reisų vidutinė galiojimo trukmė ilgesnė nei 100 menėsių
:class: info
13 savivaldybių reisų galiojimo trukmės mediana didesnė nei 100 menėsių. Tai indikacija, kad duomenys šiose savivaldybėse galimai nėra atnaujinami reguliariai.
```

```{table} Savivaldybių vietinio reguliariojo susisiekimo informacija apie reisus
:name: municipalities-trips

| Savivaldybė                   | Maršrutai | Reisai | Didžiausia reiso galiojimo data | Reisų galiojimo trukmės mediana (mėnesiais) |
|-------------------------------|-----------|--------|---------------------------------|---------------------------------------------|
| Akmenės rajono savivaldybė    | 44        | 97     | 2055-06-17                      | 297                                         |
| Alytaus miesto savivaldybė    | 19        | 955    | 2022-12-31                      | 8                                           |
| Alytaus rajono savivaldybė    | 11        | 99     | 2022-10-01                      | 13                                          |
| Anykščių rajono savivaldybė   | 31        | 184    | 2024-12-31                      | 83                                          |
| Biržų rajono savivaldybė      | 33        | 141    | 2022-10-11                      | 120                                         |
| Druskininkų savivaldybė       | 27        | 709    | 2022-10-01                      | 15                                          |
| Ignalinos rajono savivaldybė  | 35        | 100    | 2025-08-30                      | 118                                         |
| Jonavos rajono savivaldybė    | 3         | 8      | 2022-12-31                      | 107                                         |
| Jurbarko rajono savivaldybė   | 15        | 64     | 2026-12-30                      | 137                                         |
| Kalvarijos savivaldybė        | 3         | 28     | 2022-07-03                      | 85                                          |
| Kauno miesto savivaldybė      | 63        | 7320   | 2023-05-01                      | 15                                          |
| Kauno rajono savivaldybė      | 7         | 769    | 2099-12-31                      | 422                                         |
| Klaipėdos miesto savivaldybė  | 55        | 6986   | 2023-04-22                      | 15                                          |
| Klaipėdos rajono savivaldybė  | 2         | 6      | 2024-03-01                      | 78.5                                        |
| Marijampolės savivaldybė      | 18        | 323    | 2030-12-31                      | 191                                         |
| Mažeikių rajono savivaldybė   | 37        | 191    | 2024-07-22                      | 36                                          |
| Neringos savivaldybė          | 1         | 26     | 2023-01-01                      | 86                                          |
| Pakruojo rajono savivaldybė   | 46        | 125    | 2037-08-31                      | 181                                         |
| Panevėžio miesto savivaldybė  | 20        | 1694   | 2023-04-01                      | 13                                          |
| Prienų rajono savivaldybė     | 12        | 173    | 2022-10-01                      | 17                                          |
| Rokiškio rajono savivaldybė   | 29        | 185    | 2024-10-24                      | 9                                           |
| Šalčininkų rajono savivaldybė | 2         | 31     | 2099-12-31                      | 1169                                        |
| Šiaulių miesto savivaldybė    | 45        | 3089   | 2023-04-01                      | 13                                          |
| Šiaulių rajono savivaldybė    | 87        | 1779   | 2026-11-01                      | 52                                          |
| Šilutės rajono savivaldybė    | 2         | 10     | 2099-01-01                      | 1008                                        |
| Švenčionių rajono savivaldybė | 12        | 138    | 2023-10-03                      | 46                                          |
| Tauragės rajono savivaldybė   | 45        | 185    | 2022-09-07                      | 74                                          |
| Ukmergės rajono savivaldybė   | 27        | 410    | 2055-05-01                      | 121                                         |
| Utenos rajono savivaldybė     | 54        | 286    | 2033-03-23                      | 90                                          |
| Varėnos rajono savivaldybė    | 15        | 104    | 2030-12-31                      | 191                                         |
| Vilniaus miesto savivaldybė   | 99        | 25307  | 2023-04-01                      | 14                                          |
| Vilniaus rajono savivaldybė   | 80        | 1010   | 2026-08-01                      | 119                                         |
| Visagino savivaldybė          | 1         | 4      | 2022-06-01                      | 24                                          |
| Zarasų rajono savivaldybė     | 16        | 88     | 2022-06-30                      | 76                                          |
```


## Tarifai ir kainoraščiai
GTFS duomenų rinkinio failuose `fare_attributes.txt` ir `fare_rules.txt` turėtų būti pateikta su tarifais ir kainoraščiais susijusi informacija. Visgi, nė vienas VINTRA pateiktas savivaldybės failas neturi informacijos apie kainodarą. Ši informacija pateikiama tik visos šalies viešojo transporto kelionių duomenų GTFS faile.

```{admonition} Tarifai ir kainoraščiai nėra pateikiami savivaldybių VINTRA GTFS failuose
:class: warning
Nė vienas VINTRA skelbiamas atskirų savivaldybių failas neturi tarifų ir kainoraščių informacijos. Dėl šios priežasties atskirų savivaldybių duomenų failų naudotojas negali gauti informacijos apie tarifus ir kainoraščius. Tai galimai yra VINTRA trūkumas.
```

In [ ]:
# from lxml import etree
# from pathlib import Path
#
# # xsd = Path(os.path.join(working_directory, '../netex.xsd')).read_bytes()
# # schema = etree.XMLSchema(etree.XML(xsd))
# xml_validator = etree.XMLSchema(file=os.path.join(working_directory, '../netex.xsd'))
#
# # schema = etree.XMLSchema(etree.XML(xsd, base_url='https://raw.githubusercontent.com/NeTEx-CEN/NeTEx/master/xsd/NX.xsd'))
# # parser = etree.XMLParser(schema=schema)
#
#
# def validate_netex(file: str):
#     if not file:
#         return '-'
#     with ZipFile(os.path.join(netex_directory, file)) as netex_zip:
#         netex_zip_files = netex_zip.namelist()
#
#         for netex_zip_file in netex_zip_files:
#             with netex_zip.open(netex_zip_file) as netex_file:
#                 content = netex_file.read()
#                 # root = etree.fromstring(content, parser=parser)
#
#         return ', '.join(netex_zip_files)
#
#
# vintra_netex_mapping['Failas'].apply(validate_netex)